In [1]:
import pandas as pd
import seaborn as sns
import time
import re
import nltk
import math
import os
from Bio.SeqUtils.ProtParam import ProteinAnalysis
from sklearn import svm
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier
from nltk.corpus import stopwords
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_extraction.text import CountVectorizer

In [2]:
def fasta_parser(filename):
    if os.path.exists(filename):
        pass
    else:                     
        print("The file, %s, does not exist" % filename)
        
    file = open(filename,mode='r')
    rec_all = file.read()
    file.close()
    # remove all whitespace from string all_of_it
    rec_all = rec_all.replace(' ','')
    # split records by > 
    records = rec_all.split('>')
    # Parse out the headers & sequences for each record
    headers = []
    sequences = []
    for rec in records:
        s = ''
        data = rec.split('\n')
        sq = s.join(data[1:])
        if len(data[0]) > 0:
            headers.append(data[0])
   
        if (len(sq) > 0):
            sequences.append(s.join(data[1:]))
    
    return headers, sequences

In [3]:
# concatenate all relevant fasta files into one fasta file use glob
# see https://stackoverflow.com/questions/17749058/combine-multiple-text-files-into-one-text-file-using-python/17749339
# Note the code below works with no bizzare artifacts from globbing or concatenation
#read_files = glob.glob("*.fasta")

#with open("isomerase_2000.fasta", "wb") as outfile:
    #for f in read_files:
        #with open(f, "rb") as infile:
            #outfile.write(infile.read())

In [4]:
f_name_1 = 'uniprot-dnaBind-Human.fasta'
f_name_2 = 'uniprot-dnaBind-mouse.fasta'
t_head, t_seqs = fasta_parser(f_name_1)
t_head2, t_seqs2 = fasta_parser(f_name_2)

In [5]:
for hd in t_head[0:5]:
    print(hd)
    print()

sp|Q16531|DDB1_HUMANDNAdamage-bindingprotein1OS=HomosapiensOX=9606GN=DDB1PE=1SV=1
()
sp|Q92466|DDB2_HUMANDNAdamage-bindingprotein2OS=HomosapiensOX=9606GN=DDB2PE=1SV=1
()
sp|P27694|RFA1_HUMANReplicationproteinA70kDaDNA-bindingsubunitOS=HomosapiensOX=9606GN=RPA1PE=1SV=2
()
sp|Q92547|TOPB1_HUMANDNAtopoisomerase2-bindingprotein1OS=HomosapiensOX=9606GN=TOPBP1PE=1SV=3
()
sp|Q15233|NONO_HUMANNon-POUdomain-containingoctamer-bindingproteinOS=HomosapiensOX=9606GN=NONOPE=1SV=4
()


In [6]:
for sq in t_seqs[0:5]:
    print(sq)
    print()

MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTAEGLRPVKEVGMYGKIAVMELFRPKGESKDLLFILTAKYNACILEYKQSGESIDIITRAHGNVQDRIGRPSETGIIGIIDPECRMIGLRLYDGLFKVIPLDRDNKELKAFNIRLEELHVIDVKFLYGCQAPTICFVYQDPQGRHVKTYEVSLREKEFNKGPWKQENVEAEASMVIAVPEPFGGAIIIGQESITYHNGDKYLAIAPPIIKQSTIVCHNRVDPNGSRYLLGDMEGRLFMLLLEKEEQMDGTVTLKDLRVELLGETSIAECLTYLDNGVVFVGSRLGDSQLVKLNVDSNEQGSYVVAMETFTNLGPIVDMCVVDLERQGQGQLVTCSGAFKEGSLRIIRNGIGIHEHASIDLPGIKGLWPLRSDPNRETDDTLVLSFVGQTRVLMLNGEEVEETELMGFVDDQQTFFCGNVAHQQLIQITSASVRLVSQEPKALVSEWKEPQAKNISVASCNSSQVVVAVGRALYYLQIHPQELRQISHTEMEHEVACLDITPLGDSNGLSPLCAIGLWTDISARILKLPSFELLHKEMLGGEIIPRSILMTTFESSHYLLCALGDGALFYFGLNIETGLLSDRKKVTLGTQPTVLRTFRSLSTTNVFACSDRPTVIYSSNHKLVFSNVNLKEVNYMCPLNSDGYPDSLALANNSTLTIGTIDEIQKLHIRTVPLYESPRKICYQEVSQCFGVLSSRIEVQDTSGGTTALRPSASTQALSSSVSSSKLFSSSTAPHETSFGEEVEVHNLLIIDQHTFEVLHAHQFLQNEYALSLVSCKLGKDPNTYFIVGTAMVYPEEAEPKQGRIVVFQYSDGKLQTVAEKEVKGAVYSMVEFNGKLLASINSTVRLYEWTTEKELRTECNHYNNIMALYLKTKGDFILVGDLMRSVLLLAYKPMEGNFEEIARDFNPNWMSAVEILDDDNFLGAENAFNLFVCQKDSAATTDEERQHLQEVGLFHL

In [7]:
print(len(t_seqs))

39224


In [8]:
t_seqs2 = list(set(t_seqs))
print(len(t_seqs2))

37394


In [9]:
from Bio import SeqIO
#records = list(SeqIO.parse(f_name, "fasta"))


In [10]:
# human protein sequences
seq_ids_1 =[]
seqs_1 = []
#for record in SeqIO.parse("isomerase_2000.fasta", "fasta"):
for record in SeqIO.parse(f_name_1, "fasta"):
    print(repr(record.seq))
    print()
    seq_ids_1.append(record.id)
    seqs_1.append(str(record.seq))

Seq('MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTAEGLRPVKE...RIH', SingleLetterAlphabet())
()
Seq('MAPKKRPETQKTSEIVLRPRNKRSRSPLELEPEAKKLCAKGSGPSRRCDSDCLW...TRK', SingleLetterAlphabet())
()
Seq('MVGQLSEGAIAAIMQKGDTNIKPILQVINIRPITTGNSPPRYRLLMSDGLNTLS...ALM', SingleLetterAlphabet())
()
Seq('MSRNDKEPFFVKFLKSSDNSKCFFKALESIKEFQSEEYLQIITEEEALKIKEND...RVH', SingleLetterAlphabet())
()
Seq('MQSNKTFNLEKQNHTPRKHHQHHHQQQHHQQQQQQPPPPPIPANGQQASSQNEG...RRY', SingleLetterAlphabet())
()
Seq('MSEAGEATTTTTTTLPQAPTEAAAAAPQDPAPKSPVGSGAPQAAAPAPAAHVAG...SAE', SingleLetterAlphabet())
()
Seq('MTTETFVKDIKPGLKNLNLIFIVLETGRVTKTKDGHEVRTCKVADKTGSINISV...SKR', SingleLetterAlphabet())
()
Seq('MNRVNDPLIFIRDIKPGLKNLNVVFIVLEIGRVTKTKDGHEVRSCKVADKTGSI...FKR', SingleLetterAlphabet())
()
Seq('MSRDRFRSRGGGGGGFHRRGGGGGRGGLHDFRSPPPGMGLNQNRGPMGPGPGQS...PRF', SingleLetterAlphabet())
()
Seq('MKVASGSTATAAAGPSCALKAGKTASGAGEVVRCLSEQSVAISRCAGGAGARLP...LCR', SingleLetterAlphabet())
()
Seq('MGKSDFLTPKAIANRIKSKGLQKLRWYCQMCQKQCRDENGFKCHC

()
Seq('MAHATQVGLQDATSPIMEELITFHDHALMIIFLICFLVLYALFLTLTTKLTNTN...FTL', SingleLetterAlphabet())
()
Seq('MLSNRPIFPGKHYLDQLNHILGILGSPSQEDLNCIINMKARNYLQSLPSKTKVA...FQP', SingleLetterAlphabet())
()
Seq('MNRHLWKSQLCEMVQPSGGPAADQDVLGEESPLGKPAMLHLPSEQGAPETLQRC...CIE', SingleLetterAlphabet())
()
Seq('MAGYLSPAAYLYVEEQEYLQAYEDVLERYKDERDKVQKKTFTKWINQHLMKVRK...SKR', SingleLetterAlphabet())
()
Seq('RSFHHISHIAQHQRIHTGEKPYKCNECGKVFSHKSSLVNHWRIHTGEKPYKCNE...TCN', SingleLetterAlphabet())
()
Seq('MTPMRKINPLMKLINHSFIDLPTPSNISAWWNFGSLLGACLILQITTGLFLAMH...KWA', SingleLetterAlphabet())
()
Seq('MGQNLILNMNDHGFVVCAFNRTVSKVDDFLANEAKGTKVVGAQSLKEMVSKLKK...CDW', SingleLetterAlphabet())
()
Seq('MSEEQFGGDGAAAAATAAVGGSAGEQEGAMVAATQGAAAAAGSGAGTGGGTASG...TNK', SingleLetterAlphabet())
()
Seq('MSLRSGGRRRADPGADGEASRDDGATSSVSALKRLERSQWTDKMDLRFGFERLK...RRY', SingleLetterAlphabet())
()
Seq('MFGGLSGATVIDSLDTLYLMELKEEFQEAKAWVGESFHLNVSGEASLFEVNIRY...RVQ', SingleLetterAlphabet())
()
Seq('MTPMRKINPLMKLINHSFIDLPTPSNISAWWNFGSLLGACLI

Seq('MNSSPAGTPSPQPSRANGNINLGPSANPNAQPTDFDFLKVIGKGNYGKVLLAKR...FVA', SingleLetterAlphabet())
()
Seq('MRSFNQVSSAPGGASKGGGEEPGKLPEPAEEESQVLRGTGHCKWFNVRMGFGFI...KKT', SingleLetterAlphabet())
()
Seq('LLQAYGNLVNFHRMIKLTTGKEAALSYGFYGCHCGVGGRGSPKDATDR', SingleLetterAlphabet())
()
Seq('MSLQMVTVSNNIALIQPGFSLMNFDGQVFFFGQKGWPKRSCPTGVFHLDVKHNH...RGK', SingleLetterAlphabet())
()
Seq('XLRLRAALTLLGEVPRRPASRGVPGSRRTQKGSGARWEKEKHEDGVKWRQLEHK...HML', SingleLetterAlphabet())
()
Seq('MDFLWDKRTGLAARKMPHPRRYHSSERGSRGSYCEHYRSRKQATKKPFLVKRCS...ISP', SingleLetterAlphabet())
()
Seq('MRILHVNGFNGDSEKATKVQDIKNNLKEAIETIVAAMSNLVPPVELANPENQFR...WED', SingleLetterAlphabet())
()
Seq('MAMSQESLTFKDVFVDFTLEEWQQLDSAQKNLYRDVMLENYSHLVSVGYLVAKP...VQM', SingleLetterAlphabet())
()
Seq('MDLSALRVEEVQNVINAMQKILECPICLELIKEPVSTKCDHIFCKFCMLKLLNQ...IPS', SingleLetterAlphabet())
()
Seq('MASGCKIGPSILNSDLANLGAECLRMLDSGADYLHLDVMDGHFVPNITFGHPVV...ELT', SingleLetterAlphabet())
()
Seq('MATVTATTKVPEIRDVTRIERIGAHSHIRGLGLDDALEPRQLPDVVEMPW', Sing

Seq('MSRELAPLLLLLLSIHSALAMRICSFNVRSFGESKQEDKNAMDVIVKVIKRCDI...KRS', SingleLetterAlphabet())
()
Seq('XEGDEAARGQQPHQGLWRRRRTSDPSAAVNHVSSTTSLGENYEDDDLVNSDEVM...LVE', SingleLetterAlphabet())
()
Seq('LKEFPRLKSXLEDNIRRLRALADGVQKVHKGTTIANVVSGSLSISSGILTLVGM...NXN', SingleLetterAlphabet())
()
Seq('KVVQIKKSCLQSSTKQLFPDLQDLLKSIVSRMKKAVEDDVFIPLYPKSAVENKT...KED', SingleLetterAlphabet())
()
Seq('MKLLAATVLLLTICSLEGALVRRQAKEPCVESLVSQYFQTVTDYGKDLMEKVKS...ATQ', SingleLetterAlphabet())
()
Seq('MAMQMQLEANADTSVEEESFGPQPISRLEQCGINANDVKKLEEAGFHTVEAVAY...VIR', SingleLetterAlphabet())
()
Seq('RLSPPACTLRKHKTNRKPRTPFTTAQLLALERKFRQKQYLSIAERAEFSSSLSL...HLT', SingleLetterAlphabet())
()
Seq('MLLPLLLLLPMCWAVEVKRPRGVSLTNHHFYDESKPFTCLDGSATIPFDQVNDD...DEL', SingleLetterAlphabet())
()
Seq('MHGNKQHLQKDFFLYNASKARSKTYINMREVSQRFRLPPSEYVIVPSTYEPHQE...LNV', SingleLetterAlphabet())
()
Seq('MELLIMAYALKTACARNIIGVIPYFPYSKQSKMRKRGSIVCKLLASMLAKAGLT...VDE', SingleLetterAlphabet())
()
Seq('LTDRQTDTAPSPSYHLLPGRRRTVDAAASRGQGPEPAPGGGVEGV

Seq('MDSISTAILLLLLALVCLLLTLSSRDKGKLPPGPRPLSILGNLLLLCSQDMLTS...RPR', SingleLetterAlphabet())
()
Seq('MADLSLADALTEPSPDIEGEIKRDFIATLEAEAFDDVVGETVGKTDYIPLLDVD...SSN', SingleLetterAlphabet())
()
Seq('MGSAVMDTKKKKDVSSPGGSGGKKNASQKRRSLRVHIPDLSSFAMPLLDGDLEG...ETE', SingleLetterAlphabet())
()
Seq('MKKTQTWILTCIYLQLLLFNPLVKTEGICRNRVTNNVKDVTKLVANLPKDYMIT...QEV', SingleLetterAlphabet())
()
Seq('MADLANEEKPAIAPPVFVFQKDKGQKRSAGGSSPEGGEDSDREDGNYCPPVKRE...WKE', SingleLetterAlphabet())
()
Seq('MAPEIHMTGPMCLIENTNGELVANPEALKILSAITQPVVVVAIVGLYRTGKSYL...PPE', SingleLetterAlphabet())
()
Seq('XTSISVSNCQIQENVDISTVYQIFADEVLGSGQFGIVYGGKHRKTGRDVAIKVI...AFM', SingleLetterAlphabet())
()
Seq('XGRPPALLASALGLGGCVPWGAGRLRRGHGPEPDSPFRRSPPRGPASPQR', SingleLetterAlphabet())
()
Seq('XEVCQSLVKHSSGIKGSLPLQKLHLVSRSIYHSHHPTLKLQRPQLRTSFQQFSS...VRI', SingleLetterAlphabet())
()
Seq('MDFLRNLFSQTLSLGSQKERLLDELTLEGVARYMQSERCRRVICLVGAGISTSA...LAG', SingleLetterAlphabet())
()
Seq('MNIRGDIGHKAYEYQEYGPKPCKCQQPKKAFRYRPSFRTQERDHTGEKPNACK',

...

Seq('MQARYSVSSPNSLGVVPYLGGEQSYYRAAAAAAGGGYTAMPAPMSVYSHPAHAE...SKF', SingleLetterAlphabet())
()
Seq('MAAVVQQNDLVFEFASNVMEDERQLGDPAIFPAVIVEHVPGADILNSYAGLACV...NSF', SingleLetterAlphabet())
()
Seq('MSSKQEIMSDQRFRRVAKDPRFWEMPEKDRKVKIDKRFRAMFHDKKFKLNYAVD...KVK', SingleLetterAlphabet())
()
Seq('MEKQRALVAAKDGDVATLERLLEAGALGPGITDALGAGLVHHATRAGHLDCVKF...FGE', SingleLetterAlphabet())
()
Seq('MKPGFSPRGGGFGGRGGFGDRGGRGGRGGFGGGRGRGGGFRGRGRGGGGGGGGG...VKN', SingleLetterAlphabet())
()
Seq('MSEPGGGGGEDGSAGLEVSAVQNVADVSVLQKHLRKLVPLLLEDGGEAPAALEA...CTE', SingleLetterAlphabet())
()
Seq('MSSEQDKSASKEKSKKPVRFLPQLSMEKLASKEKFKAPARALPQLSMVSTKPHW...LNS', SingleLetterAlphabet())
()
Seq('MGILSFLPVLATESDWADCKSPQPWGHMLLWTAVLFLAPVAGTPAAPPKAVLKL...NRI', SingleLetterAlphabet())
()
Seq('MSQQRPARKLPSLLLDPTEETVRRRCRDPINVEGLLPSKIRINLEDNVQYVSMR...VSN', SingleLetterAlphabet())
()
Seq('MWQLLLPTALLLLVSAGMRTEDLPKAVVFLEPQWYRVLEKDSVTLKCQGAYSPE...QDK', SingleLetterAlphabet())
()
Seq('MDEGGTPLLPDSLVYQIFLSLGPADVLAAGLVCRQWQAVSRDEFL

Seq('MASQLQVFSPPSVSSSAFCSAKKLKIEPSGWDVSGQSSNDKYYTHSKTLPATQG...SYL', SingleLetterAlphabet())
()
Seq('MEEKQQIILANQDGGTVAGAAPTFFVILKQPGNGKTDQGILVTNQDACALASSV...AGK', SingleLetterAlphabet())
()
Seq('MAQSPPPQSLLGHDHWIFAQGWGWAGHWDSTSPASSSDSSGSCPCDGARGLPQP...IFY', SingleLetterAlphabet())
()
Seq('MQIPRAALLPLLLLLLAAPASAQLSRAGRSAPLAAGCPDRCEPARCPPQPEHCE...IDP', SingleLetterAlphabet())
()
Seq('MALSSQIWAACLLLLLLLASLTSGSVFPQQTGQLAELQPQDRAGARASWMPMFQ...CKT', SingleLetterAlphabet())
()
Seq('MCNTNMSVPTDGAVTTSQIPASEQETLVRPKPLLLKLLKSVGAQKDTYTMKEVL...YFP', SingleLetterAlphabet())
()
Seq('MGLGPVFLLLAGIFPFAPPGAAAEPHSLRYNLTVLSWDGSVQSGFLTEVHLDGQ...EGA', SingleLetterAlphabet())
()
Seq('MTDRFWDQWYLWYLRLLRLLDRGSFRNDGLKASDVLPILKEKVAFVSGGRDKRG...QGT', SingleLetterAlphabet())
()
Seq('MELRVGNRYRLGRKIGSGSFGDIYLGTDIAAGEEVAIKLECVKTKHPQLHIESK...VHR', SingleLetterAlphabet())
()
Seq('MGKEIQLKPKANVSSYVHFLLNYRNKFKEQQPNTYVGFKEFSRKCSEKWRSISK...RQS', SingleLetterAlphabet())
()
Seq('MAGGKAGKDSGKAKAKAVSRSQRAGLQFPVGRIHRHLKTRTTSHG

Seq('MALPRLTGALRSFSNVTKQDNYNEEVADLKIKRSKLHEQVLDLGLTWKKIIKFL...ALK', SingleLetterAlphabet())
()
Seq('MEPLQQQQQQQQQQQKQPHLAPLQMDAREKQGQQMREAQFLYAQKLVTQPTLLS...WSL', SingleLetterAlphabet())
()
Seq('MELLCHEVDPVRRAVRDRNLLRDDRVLQNLLTIEERYLPQCSYFKCVQKDIQPY...IDL', SingleLetterAlphabet())
()
Seq('MFGSSRYLGSSEQPRANSLGPSDRTLVLCSLVEGEDKVNPSEPHGLRMEEKWLL...HLQ', SingleLetterAlphabet())
()
Seq('MVDQLRERTTMADPLRERTELLLADYLGYCAREPGTPEPAPSTPEAAVLRSAAA...RLL', SingleLetterAlphabet())
()
Seq('MMDSPFLELWQSKAVSIREQLGLGDRPNDSYCYNSAKNSTVLQGVTFGGIPTVL...QEA', SingleLetterAlphabet())
()
Seq('MEQGKGLAVLILAIILLQGTLAQSIKGNHLVKVYDYQEDGSVLLTCDAEAKNIT...RRN', SingleLetterAlphabet())
()
Seq('MSVFLGPGMPSASLLVNLLSALLILFVFGETEIRFTGQTEFVVNETSTTVIRLI...THL', SingleLetterAlphabet())
()
Seq('MWTSGRMSNAKNWLGLGMSLYFWGLMDLTTTVLSDTPTPQGELEALLSDKPQSH...PLW', SingleLetterAlphabet())
()
Seq('MDEEYDVIVLGTGLTECILSGIMSVNGKKVLHMDRNPYYGGESSSITPLEELYK...AEQ', SingleLetterAlphabet())
()
Seq('MTFRATDSEFDLTNIEEYAENSALSRLNNIKAKQRVSYVTSTENE

Seq('MPKCPKCNKEVYFAERVTSLGKDWHRPCLKCEKCGKTLTSGGHAEHEGKPYCNH...TFK', SingleLetterAlphabet())
()
Seq('MTLQELVHKAASCYMDRVAVCFDECNNQLPVYYTYKTVVNAASELSNFLLLHCD...NQK', SingleLetterAlphabet())
()
Seq('MAGASELGTGPGAAGGDGDDSLYPIAVLIDELRNEDVQLRLNSIKKLSTIALAL...ALA', SingleLetterAlphabet())
()
Seq('MGSAVMDTKKKKDVSSPGGSGGKKNASQKRRSLRVHIPDLSSFAMPLLDGDLEG...ETE', SingleLetterAlphabet())
()
Seq('MCEEEDSTALVCDNGSGLCKAGFAGDDAPRAVFPSIVGRPRHQGVMVGMGQKDS...KCF', SingleLetterAlphabet())
()
Seq('MDPQTAPSRALLLLLFLHLAFLGGRSHPLGSPGSASDLETSGLQEQRNHLQGKL...RRH', SingleLetterAlphabet())
()
Seq('MHLSQLLACALLLTLLSLRPSEAKPGAPPKVPRTPPAEELAEPQAAGGGQKKGD...LGC', SingleLetterAlphabet())
()
Seq('MFTIKLLLFIVPLVISSRIDQDNSSFDSLSPEPKSRFAMLDDVKILANGLLQLG...SFE', SingleLetterAlphabet())
()
Seq('MAAAEAANCIMENFVATLANGMSLQPPLEEVSCGQAESSEKPNAEDMTSKDYYF...RMR', SingleLetterAlphabet())
()
Seq('MAMVSEFLKQAWFIENEEQEYVQTVKSSKGGPGSAVSPYPTFNPSSDVAALHKA...GGN', SingleLetterAlphabet())
()
Seq('MAELQMLLEEEIPGGRRALFDSYTNLERVADYCENNYIQSADKQR

()
Seq('MASPTLSPDSSSQEALSAPTCSPTSDSENLSPDELELLAKLEEQNRLLEADSKS...LDN', SingleLetterAlphabet())
()
Seq('MAEAEGESLESWLNKATNPSNRQEDWEYIIGFCDQINKELEGPQIAVRLLAHKI...GNL', SingleLetterAlphabet())
()
Seq('MTANGTAEAVQIQFGLINCGNKYLTAEAFGFKVNASASSLKKKQIWTLEQPPDE...WEY', SingleLetterAlphabet())
()
Seq('MGFSSELCSPQGHGVLQQMQEAELRLLEGMRKWMAQRVKSDREYAGLLHHMSLQ...RHR', SingleLetterAlphabet())
()
Seq('MFGAAGRQPIGAPAAGNSWHFSRTMEELVHDLVSALEESSEQARGGFAETGDHS...KSA', SingleLetterAlphabet())
()
Seq('MASATAAAARRGLGRALPLFWRGYQTERGVYGYRPRKPESREPQGALERPPVDH...TFA', SingleLetterAlphabet())
()
Seq('MEEEGLECPNSSSEKRYFPESLDSSDGDEEEVLACEDLELNPFDGLPYSSRYYK...TLQ', SingleLetterAlphabet())
()
Seq('MESGPKMLAPVCLVENNNEQLLVNQQAIQILEKISQPVVVVAIVGLYRTGKSYL...LPF', SingleLetterAlphabet())
()
Seq('MDDKGDPSNEEAPKAIKPTSKEFRKTWGFRRTTIAKREGAGDAEADPLEPPPPQ...SQA', SingleLetterAlphabet())
()
Seq('MPSPRPVLLRGARAALLLLLPPRLLARPSLLLRRSLSAASCPPISLPAAASRSS...IEE', SingleLetterAlphabet())
()
Seq('MRFRFGVVVPPAVAGARPELLVVGSRPELGRWEPRGAVRLRP

In [11]:
# mouse protein sequences
seq_ids_2 =[]
seqs_2 = []
#for record in SeqIO.parse("isomerase_2000.fasta", "fasta"):
for record in SeqIO.parse(f_name_2, "fasta"):
    print(repr(record.seq))
    print()
    seq_ids_2.append(record.id)
    seqs_2.append(str(record.seq))

Seq('MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTAEGLRPVKE...RIH', SingleLetterAlphabet())
()
Seq('MSRNDQEPFLVKFLKSSDNSECFFKALESIKELQSEDYLQIITDEEALKIREND...RVH', SingleLetterAlphabet())
()
Seq('MKVASGSAAAAAGPSCSLKAGRTAGEVVLGLSEQSVAISRCAGTRLPALLDEQQ...IAI', SingleLetterAlphabet())
()
Seq('MKALSPVRGCYEAVCCLSERSLAIARGRGKSPSTEEPLSLLDDMNHCYSRLREL...FCH', SingleLetterAlphabet())
()
Seq('MKAFSPVRSVRKNSLSDHSLGISRSKTPVDDPMSLLYNMNDCYSKLKELVPSIP...LCG', SingleLetterAlphabet())
()
Seq('MGKSDFLSPKAIANRIKSKGLQKLRWYCQMCQKQCRDENGFKCHCMSESHQRQL...KLA', SingleLetterAlphabet())
()
Seq('MAPKKCPETQKSPDVAVLLRSKSRRGPQELEPEAKKLRVQGPVSSRTCESCCLL...ERL', SingleLetterAlphabet())
()
Seq('MKAVSPVRPSGRKAPSGCGGGELALRCLAEHGHSLGGSAAAAAAAAAARCKAAE...LCR', SingleLetterAlphabet())
()
Seq('MFAKGKGSAVPSDGQAREKLALYVYEYLLHVGAQKSAQTFLSEIRWEKNITLGE...MSV', SingleLetterAlphabet())
()
Seq('MAWSGNKAAVVLCVDVGVAMGNSFPGEESPIEQAKKVMTMFVQRQVFSESKDEI...DMI', SingleLetterAlphabet())
()
Seq('MSEWESYYKTEGEEEEEEEESPDTGGEYKYSGRDSLIFLVDASRA

Seq('MEKEEETTRELLLPNWQGSGSHGLTIAQRDDGVFVQEVMQNSPAARTGVVKEGD...AGL', SingleLetterAlphabet())
()
Seq('MERVNDASCGPSGCYTYQVSRHSTEMLHNLNQQRKNGGRFCDVLLRVGDESFPA...EGK', SingleLetterAlphabet())
()
Seq('MIATGALLRVLLLLLAFGHSTYGAECDPPCDPQYGFCEADNVCRCHVGWEGPLC...EEI', SingleLetterAlphabet())
()
Seq('MDRLGSFSNDPSDKPPCRGCSSYLTEPYIKCAECGPPPFFLCLQCFTRGFEYKK...KER', SingleLetterAlphabet())
()
Seq('XTGLPRNTTISLLTTDDAMVSIDPTMPANSERTPYKVRPVAVKQVSEREELIQG...KRQ', SingleLetterAlphabet())
()
Seq('MDISTRSKDPVSTEKTAPKRRFPSPPHSSNGHSPQDSSTSPIKKKKK', SingleLetterAlphabet())
()
Seq('MASDSPARSLDEIDLSALRDPAGIFELVELVGNGTYGQVYKGRHVKTGQLAAIK...MNW', SingleLetterAlphabet())
()
Seq('MSGTRASNDRPPGTGGVKRGRLQQEAAATGSRVTVVLGAQWGDEGKGKVVDLLA...QLF', SingleLetterAlphabet())
()
Seq('XDGVSLDSGGPDDRISVDSDGSDSFVMLLESGHCLILKKILVVLRLQGHLTRNL...YWS', SingleLetterAlphabet())
()
Seq('MAGKAAAPGTAVLLVTANVGSLFDDPENLQKNWLREFYQVLHTHKPHFMALHCQ...SSS', SingleLetterAlphabet())
()
Seq('MGFAGFFPEESLQRCDAGNVQEPHCYRYICNCGYKPCENEDHGKKQCSFACNSF...G

Seq('MRVQDTSGTYYWHIPTGTTQWEPPGRASPSQGSSPQEESQLTWTGFAHQEGFEE...WVE', SingleLetterAlphabet())
()
Seq('MNRPPLSDKVQTQLNTEQLIDDVVAKRTRQWRTSTTNGGILTVSIDNPGAVQCP...TVG', SingleLetterAlphabet())
()
Seq('MDAPWRQVAAGRGRARGRATAVPLSGNGVPFGGAGGGRAKGSGGAVSSGPGPGG...WPW', SingleLetterAlphabet())
()
Seq('MEVAPEQPRWMAHPAVLNAQHPDSHHPGLAHNYM', SingleLetterAlphabet())
()
Seq('MPPCPPQQNRNRLSQLPVGELGEMELTWQEIMSITELQGLNVPSETSFEPQAPT...SLM', SingleLetterAlphabet())
()
Seq('XGQAESPLGIRPQQMTKDVWDYVFFKDAPFPKTQIPKEKLDQLKQEFEFWYPVD...QSF', SingleLetterAlphabet())
()
Seq('MGLPSTWRYGRGPGIGTVTMVSWGRFICLVLVTMATLSLARPSFSLVEDTTLEP...VKT', SingleLetterAlphabet())
()
Seq('MESEKPKKTQEMKTDLKLLLECLKYHMGNPLSQKEVLITIHSVCKQNSDAGIYF...AAL', SingleLetterAlphabet())
()
Seq('XGARGNTVLPDPGTPDQHQACQTHPTFPVGPQPLLTAQQLASAVAGVMPGGPPA...ENC', SingleLetterAlphabet())
()
Seq('MSSSESVKSLTELVQQPCPAIETSKEGKPPEPSDPPASDSQPTTPLPLSGHSAL...WEF', SingleLetterAlphabet())
()
Seq('FTQLQMVGLIFELMSAGLLQNLWLGSAHSCLLEVKRRLDLETDHQYLAGSSGPF...LDF', SingleLe

Seq('MYGKASKGCAPSDGQAREKLALYVYEYLLHVGAQKSAQTFLSEIRWEKNITLAS...PAL', SingleLetterAlphabet())
()
Seq('MAASLPSTLSFSSAPDEIQHPQIKFSEWKFKLFRVRSFEKAPEEAQKEKDSSEG...MEF', SingleLetterAlphabet())
()
Seq('MQVWYIQDLQRQPVHPKYYGQLCSGNCYLVLYTYQKLGCVQYLLYLWQGNAGNK...GFF', SingleLetterAlphabet())
()
Seq('MKGDSRHLNEEEGASGYEECIIVNGNFSDQSSDTKDAPSPPVLEAICTEPVCTP...ACE', SingleLetterAlphabet())
()
Seq('XPYPSGKLHMGHVRVYTLSDTIARFQKMRGMQVINPMGWDAFGLPAENAAIERN...EKA', SingleLetterAlphabet())
()
Seq('MQQFFGLEATGQLDNSTLAIMHIPRCGVPDVQHLRAVPQRSRWMKRYLTYRIYN...KAF', SingleLetterAlphabet())
()
Seq('IAFTPESQRRSSSGSTDSEESTDSEEEDGAKQDLFESSSANTEDKMEVDLNEPP...GPV', SingleLetterAlphabet())
()
Seq('MSVSALSLTRFAGSLSGFLQVASVFCLLLLLVKAVQVYLHRKWLLKALQQFPSP...KVH', SingleLetterAlphabet())
()
Seq('XLGVQGALLSHFIQPVYISSILVGDGNCNDTRGLEIAINQRVDDALTSKLPMFY...FQI', SingleLetterAlphabet())
()
Seq('MVTFRDVAVVFSEEELGLLDAAQRKLYHDVMLENFRMLLSVGDKNPEEMESLEE...QTL', SingleLetterAlphabet())
()
Seq('LKIKLGLLGGKRKKAGSSEEGHEPEAEESDLDSGSVHSASGWPDG

Seq('VTAGDSEVEAAAQAAGIHDAILSFPEVCTNRTTIVIAHRLSTVVNADQILVIKD...DTA', SingleLetterAlphabet())
()
Seq('XSRVLGEQAETAGADRQPRPRPGGGGRERGRECISVHVGQAGVQMGNACWELYC...GEE', SingleLetterAlphabet())
()
Seq('ALGPWTRVYSTSPAFAEVLRLPQKQLTKVVYPLRELGQHLAADSGPGLIEQRLF...SLK', SingleLetterAlphabet())
()
Seq('METMFQETQYPDVLTREVLARSMDGSEAKVQIRFNNRRAKQRAREKKAMLRSTA...QEP', SingleLetterAlphabet())
()
Seq('MAATSEGPLFAASIEKTWGSVVRSPEGTPQKVRELIDEGIVPEEGGTEPKDTAA...SSS', SingleLetterAlphabet())
()
Seq('MLLPGLLLLLLLLAGTRWLWGQWKLRKLHLPPLAPGFLHFLQPNLPIYLLGLTQ...ERP', SingleLetterAlphabet())
()
Seq('MSDDKPFLCTAPGCGQRFTNEDHLAVHKHKHEMTLKFGPARNDSVIVADQTPTP...AAV', SingleLetterAlphabet())
()
Seq('MGWSWIFLFLLSGTAGVLSEVQLQQSGPELVKPGASVKISCKASGYTFTDYYMN...CAR', SingleLetterAlphabet())
()
Seq('MAKDVIGTPQRPAASNTIVVGSPHTPNTHFVSQNQTSDSSPWSAGKRNRKGEKN...KEK', SingleLetterAlphabet())
()
Seq('MTEELITPVYCTGVSAQVQKKRDKELGLGRHENAIKYLGQDYETLRARCLQSGV...GVV', SingleLetterAlphabet())
()
Seq('MRAWIFFLLCLAGRALAAPQTEVAEEIVEEETVVEETGVPVGANP

...

()
Seq('MAQAHPRSGTRLFRTYAARGVRGSQRQPGGLAEQWFQPPNLKRAFSSSLSDSNE...LFR', SingleLetterAlphabet())
()
Seq('MERTELLKPRTLADLIRILHELFAGDEVNVEEVQAVLEAYESNPAEWALYAKFD...ENN', SingleLetterAlphabet())
()
Seq('MLDPSSSEEESDEILEEERGKDVLGSAASGARLSPSRTSEGSAGSAGMGGSGAG...EDD', SingleLetterAlphabet())
()
Seq('MAEQEGSGLQMLLHTLQNSSDKASTLSILQVLGDLLSVGTDRRIYYMISKGGSE...SVT', SingleLetterAlphabet())
()
Seq('MAAASGYTDLREKLKSMTSRDNYKAGSREAAAAAAAAVAAAAAAAAAAEPYPAS...RRH', SingleLetterAlphabet())
()
Seq('MTTPLMGVMPTSLRATLQNCSRGNQQEGLFSPKAMGRMAGQKDSTKPRDEVFHP...STA', SingleLetterAlphabet())
()
Seq('MLDLEVVPERSLGNEQWEFTLGMPLAQAVAILQKHCRIIRNVQVLYSEQSPLSH...ELP', SingleLetterAlphabet())
()
Seq('MAANVGSMSQYWKRFDLQQLQRELDAAATVLANRQDESEQSRKRLIEQSREFKK...LWQ', SingleLetterAlphabet())
()
Seq('MGRVQLFEIRLSQGRVVYGPGEPLAGTVHLRLGAPLPFRAIRVTCMGSCGVSTK...PGS', SingleLetterAlphabet())
()
Seq('MNAETCVSYCESPAAAMDAYYSPVSQSREGSSPFRGFPGGDKFGTTFLSAGAKG...WAT', SingleLetterAlphabet())
()
Seq('MSGTQSTITDRFPLKKPIRHGSILNRESPTDKKQKVERSSSH

Seq('MSTTSKESLVCNLRQLKCHFTWNLIAEDESLDEFEDRVFNKDEFQNSEFKATMC...AEY', SingleLetterAlphabet())
()
Seq('MDIATGPESLERCFPRGQTDCAKMLDGIKMEEHALRPGPATLGVLLGSDCPHPA...FAS', SingleLetterAlphabet())
()
Seq('MRFLILFLALSLGEIDAAPPVQSRIVGGFNCEKNSQPWHVAVFRYNKYICGGVL...KNP', SingleLetterAlphabet())
()
Seq('MQSPAVLRTSRQVQNAHTGLDLSVPQHQEVRGKMMSGHVEYQILVVTRLAVFKS...SLF', SingleLetterAlphabet())
()
Seq('MEGEGGGSGGAGTSGDSGDGGEQLLTVKHELRTANLTGHAEKVGIENFELLKVL...FSD', SingleLetterAlphabet())
()
Seq('MSGRGKQGGKARAKAKTRSSRAGLQFPVGRVHRLLRKGNYSERVGAGAPVYLAA...KGK', SingleLetterAlphabet())
()
Seq('MAAGVAAWLPFARAAAIGWMPVASGPMPAPPRQERKRTQDALIVLNVSGTRFQT...SAL', SingleLetterAlphabet())
()
Seq('MPVMKGLLAPQNTFLDTIATRFDGTHSNFILANAQVAKGFPIVYCSDGFCELAG...INV', SingleLetterAlphabet())
()
Seq('MNGLPATEAPGGAGCALAGLPPLPRGLSGLLNASGGSWRELERVYSQRSRIHDE...ISL', SingleLetterAlphabet())
()
Seq('MSLCVAPRHPTGAAAALGLGSLLVLLGPGRACPAGCACTDPHTVDCRDRGLPSV...EDD', SingleLetterAlphabet())
()
Seq('MSEFWLCFNCCIAEQPQPKRRRRIDRSMIGEPTNFVHTAHVGSGD

Seq('MNLAANRAPGRRRLPLPSPSLCQLLRVWGLLSLLPGSARVQAAEQRQVFQVMEE...QYV', SingleLetterAlphabet())
()
Seq('MAFSGKYEFESEKNYDEFMKRLGLPGDVIERGRNFKIITEVQQDGQDFTWSQSY...RLA', SingleLetterAlphabet())
()
Seq('MMVDCQSSTQEIGEELINGVIYSISLRKVQLHQGATKGQRWLGCENESALNLYE...GIF', SingleLetterAlphabet())
()
Seq('MAALKEARSYGLSCGRVSDGSRVSVFHVKLTDSALKAFESYRAHQDSVSLRPSI...AWP', SingleLetterAlphabet())
()
Seq('MMVESASETIRSAPSGQNGVGSLSAQADGGGGAGTAGTAPAAGRDASGREAASG...DWV', SingleLetterAlphabet())
()
Seq('MARPCAFLMVLVVLSYWSACSLGCDLPQTHNLRNKRALTLLEQMRRLSPLSCLK...KEE', SingleLetterAlphabet())
()
Seq('MMSDASDMLAAALEQMDGIIAGSKALEYSNGIFDCQSPTSPFMGSLRALHLVED...SNV', SingleLetterAlphabet())
()
Seq('MTGGRFDFDDGGTYCGGWEEGKAHGHGICTGPKGQGEYSGSWSHGFEVVGVYTW...FLT', SingleLetterAlphabet())
()
Seq('MTTTIRQFTSSSSIKGSSGLGGGSSRTSCRLSGSLGAGSCRLGSASGLGSALGS...TTR', SingleLetterAlphabet())
()
Seq('MTTLTRQDLNFGQVVADVLSEFLEVAVHLILYVREVYPVGIFQKRKKYNVPVQM...KNS', SingleLetterAlphabet())
()
Seq('MSHRTSSAFRAERSFRSSSSSSSSSSSSASRALPAQDPPMEKALS

Seq('MVKREINVCQQTWALLCKNLLRKKRLKRDTFLEFLYTALILLSLILFLQLHEVY...EEA', SingleLetterAlphabet())
()
Seq('MRKRHLRLGQQMWALLCKNWLRKFRMRRETLLEWLFSLLLILFVYQLSSNLHQV...EEL', SingleLetterAlphabet())
()
Seq('MGMKHSSRCLLLRRKMAENAVESTEVSSAPPQPPQPVIPAKPVQCVHHVSTQPS...KMR', SingleLetterAlphabet())
()
Seq('MFLKFCLWTMFFFSAWSPIGHAKYSSLLEVVTPLRVTVTRGNNISPGWLSYSLN...LSK', SingleLetterAlphabet())
()
Seq('MAQKEEAAEAAAPASQNGDDLENLEDPEKLKELIDLPPFEIVTGVRLPVNFFKF...ILK', SingleLetterAlphabet())
()
Seq('MEKSVAETENGDAFLELKKLPTSKSPHRYTKEELLDIKERPYSKQRPSCLSEKY...YRQ', SingleLetterAlphabet())
()
Seq('MSYPGYPPPAGGYPPAAPGGGPWGGAGYPPPSMPPIGLDNVANYAGQFNQDYLS...GND', SingleLetterAlphabet())
()
Seq('MSDSLVVCEVDPELKETLRKFRFRKETNNAAIIMKVDKDRQMVVLEDELQNISP...FFR', SingleLetterAlphabet())
()
Seq('MLLAAMCLALLGCLQAQELKGHVSIILLGATGDLAKKYLWQGLFQLYLDEAGKG...FLG', SingleLetterAlphabet())
()
Seq('MGSGISSESKESARRSKELEKKLQEDAERDARTVKLLLLGAGESGKSTIVKQMK...GLF', SingleLetterAlphabet())
()
Seq('MSVPAFIDISEEDQAAELRAYLKSKGAELSEENSEGGLHVDLAQI

Seq('MSSAPRRPASGADSLHTPEPESLSPGTPGFPEQEEDELRTLGVERFEEILQEAG...MPV', SingleLetterAlphabet())
()
Seq('MATPASTPDTRALVADFVGYKLRQKGYVCGAGPGEGPAADPLHQAMRAAGDEFE...ASK', SingleLetterAlphabet())
()
Seq('MAASAKRKQEEKHLKMLRDMTGLPHNRKCFDCDQRGPTYVNMTVGSFVCTSCSG...PFL', SingleLetterAlphabet())
()
Seq('MGTVLSLSPASSAKGRRPGGLPEEKKKAPPAGDEALGGYGAPPAGKGGKGESRL...LDR', SingleLetterAlphabet())
()
Seq('MSVDEKPGSPMYVYESTVHCANILLGLNDQRKKDILCDVTLIVERKEFRAHRAV...DYA', SingleLetterAlphabet())
()
Seq('MANNASLEQDPNHCSAINNSIPLIQGKLPTLTVSGKIRVTVTFFLFLLSTAFNA...FSL', SingleLetterAlphabet())
()
Seq('MKAGCSIVEKPEGGGGYQFPDWAYKAESSPGSRQIQLWHFILELLQKEEFRHVI...ADA', SingleLetterAlphabet())
()
Seq('MPRSFLVKSKKAHSYHQPRSPGPDYSLRLETVPAPGRAEGGAVSAGESKMEPRE...GLK', SingleLetterAlphabet())
()
Seq('MALLLVSLLAFLGSGSGCHHWLCHCSNRVFLCQDSKVTEIPPDLPRNAIELRFV...VQN', SingleLetterAlphabet())
()
Seq('MLRFLRRTFGRRSMQRYARGAAGRGAAGLGDERDGGPRGGPAAAASSSVLPAAP...TAL', SingleLetterAlphabet())
()
Seq('MEANGFGLQNFPELKNDTFLRAAWGEETDYTPVWCMRQAGRYLPE

In [12]:
#print(len(seq_ids))
#print()
#print(len(seqs))

In [13]:
seqs_1[0:3]

['MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTAEGLRPVKEVGMYGKIAVMELFRPKGESKDLLFILTAKYNACILEYKQSGESIDIITRAHGNVQDRIGRPSETGIIGIIDPECRMIGLRLYDGLFKVIPLDRDNKELKAFNIRLEELHVIDVKFLYGCQAPTICFVYQDPQGRHVKTYEVSLREKEFNKGPWKQENVEAEASMVIAVPEPFGGAIIIGQESITYHNGDKYLAIAPPIIKQSTIVCHNRVDPNGSRYLLGDMEGRLFMLLLEKEEQMDGTVTLKDLRVELLGETSIAECLTYLDNGVVFVGSRLGDSQLVKLNVDSNEQGSYVVAMETFTNLGPIVDMCVVDLERQGQGQLVTCSGAFKEGSLRIIRNGIGIHEHASIDLPGIKGLWPLRSDPNRETDDTLVLSFVGQTRVLMLNGEEVEETELMGFVDDQQTFFCGNVAHQQLIQITSASVRLVSQEPKALVSEWKEPQAKNISVASCNSSQVVVAVGRALYYLQIHPQELRQISHTEMEHEVACLDITPLGDSNGLSPLCAIGLWTDISARILKLPSFELLHKEMLGGEIIPRSILMTTFESSHYLLCALGDGALFYFGLNIETGLLSDRKKVTLGTQPTVLRTFRSLSTTNVFACSDRPTVIYSSNHKLVFSNVNLKEVNYMCPLNSDGYPDSLALANNSTLTIGTIDEIQKLHIRTVPLYESPRKICYQEVSQCFGVLSSRIEVQDTSGGTTALRPSASTQALSSSVSSSKLFSSSTAPHETSFGEEVEVHNLLIIDQHTFEVLHAHQFLQNEYALSLVSCKLGKDPNTYFIVGTAMVYPEEAEPKQGRIVVFQYSDGKLQTVAEKEVKGAVYSMVEFNGKLLASINSTVRLYEWTTEKELRTECNHYNNIMALYLKTKGDFILVGDLMRSVLLLAYKPMEGNFEEIARDFNPNWMSAVEILDDDNFLGAENAFNLFVCQKDSAATTDEERQHLQEVGLF

In [14]:
seqs_2[0:3]

['MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTAEGLRPVKEVGMYGKIAVMELFRPKGESKDLLFILTAKYNACILEYKQSGESIDIITRAHGNVQDRIGRPSETGIIGIIDPECRMIGLRLYDGLFKVIPLDRDNKELKAFNIRLEELHVIDVKFLYGCQAPTICFVYQDPQGRHVKTYEVSLREKEFNKGPWKQENVEAEASMVIAVPEPFGGAIIIGQESITYHNGDKYLAIAPPIIKQSTIVCHNRVDPNGSRYLLGDMEGRLFMLLLEKEEQMDGTVTLKDLRVELLGETSIAECLTYLDNGVVFVGSRLGDSQLVKLNVDSNEQGSYVVAMETFTNLGPIVDMCVVDLERQGQGQLVTCSGAFKEGSLRIIRNGIGIHEHASIDLPGIKGLWPLRSDPGRETDDTLVLSFVGQTRVLMLNGEEVEETELMGFVDDQQTFFCGNVAHQQLIQITSASVRLVSQEPKALVSEWKEPQGKNISVASCNSSQVVVAVGRALYYLQIHPQELRQISHTEMEHEVACLDITPLGDSNGLSPLCAIGLWTDISARILKLPSFELLHKEMLGGEIIPRSILMTTFESSHYLLCALGDGALFYFGLNIETGLLSDRKKVTLGTQPTVLRTFRSLSTTNVFACSDRPTVIYSSNHKLVFSNVNLKEVNYMCPLNSDGYPDSLALANNSTLTIGTIDEIQKLHIRTVPLYESPRKICYQEVSQCFGVLSSRIEVQDSSGGTTALRPSASTQALSSSVSSSKLFSSSTAPHETSFGEEVEVHNLLIIDQHTFEVLHAHQFLQNEYALSLVSCKLGKDPNTYFIVGTAMVYPEEAEPKQGRIVVFQYSDGKLQTVAEKEVKGAVYSMVEFNGKLLASINSTVRLYEWTTEKELRTECNHYNNIMALYLKTKGDFILVGDLMRSVLLLAYKPMEGNFEEIARDFNPNWMSAVEILDDDNFLGAENAFNLFVCQKDSAATTDEERQHLQEVGLF

In [15]:
#seqID = []
#for item in records:
    #seqID.append(item.id)
    #print(item.id)
    #print()

## Create pandas dataframe using seqID & sequences

In [16]:
# create dataframe of 2000 additional isomerase sequences
#d_iso = {'name':seq_ids,'sequence':seqs}
#d_1 = {'name':seqID,'sequence':t_seqs}
#df = pd.DataFrame(d_1)
#df.head()

In [17]:
d_1 = {'name':seq_ids_1,'sequence':seqs_1}
# create dataframe from dictionary
df1 = pd.DataFrame(d_1)
df1.head()

name                                           sequence
0   sp|Q16531|DDB1_HUMAN  MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTA...
1   sp|Q92466|DDB2_HUMAN  MAPKKRPETQKTSEIVLRPRNKRSRSPLELEPEAKKLCAKGSGPSR...
2   sp|P27694|RFA1_HUMAN  MVGQLSEGAIAAIMQKGDTNIKPILQVINIRPITTGNSPPRYRLLM...
3  sp|Q92547|TOPB1_HUMAN  MSRNDKEPFFVKFLKSSDNSKCFFKALESIKEFQSEEYLQIITEEE...
4   sp|Q15233|NONO_HUMAN  MQSNKTFNLEKQNHTPRKHHQHHHQQQHHQQQQQQPPPPPIPANGQ...

In [18]:
d_2 = {'name':seq_ids_2,'sequence':seqs_2}
# create dataframe from dictionary
df2 = pd.DataFrame(d_2)
df2.head()

name                                           sequence
0   sp|Q3U1J4|DDB1_MOUSE  MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTA...
1  sp|Q6ZQF0|TOPB1_MOUSE  MSRNDQEPFLVKFLKSSDNSECFFKALESIKELQSEDYLQIITDEE...
2    sp|P20067|ID1_MOUSE  MKVASGSAAAAAGPSCSLKAGRTAGEVVLGLSEQSVAISRCAGTRL...
3    sp|P41133|ID3_MOUSE  MKALSPVRGCYEAVCCLSERSLAIARGRGKSPSTEEPLSLLDDMNH...
4    sp|P41136|ID2_MOUSE  MKAFSPVRSVRKNSLSDHSLGISRSKTPVDDPMSLLYNMNDCYSKL...

In [19]:
df1.shape

(39224, 2)

In [20]:
df2.shape

(23792, 2)

In [21]:
# remove non-coding amino acid letters like X,B,U
df1['sequence'] = df1['sequence'].str.replace('U','G')
df1['sequence'] = df1['sequence'].str.replace('X','G')
df1['sequence'] = df1['sequence'].str.replace('B','G')

In [22]:
# remove non-coding amino acid letters like X,B,U
df2['sequence'] = df2['sequence'].str.replace('U','G')
df2['sequence'] = df2['sequence'].str.replace('X','G')
df2['sequence'] = df2['sequence'].str.replace('B','G')

In [23]:
#df['MW'] = df['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df.head()

In [24]:
#df2['MW'] = df2['sequence'].apply(lambda seq: ProteinAnalysis(seq).molecular_weight())
#df2.head()

In [25]:
# Create 2 columns for the 2 dataframes
df1['classification'] = 'DNA BINDING'
df1['type'] = 12

df2['classification'] = 'DNA BINDING'
df2['type'] = 12

# concat the 2 dataframes
df = pd.concat([df1,df2])

df.head(10)

name                                           sequence  \
0   sp|Q16531|DDB1_HUMAN  MSYNYVVTAQKPTAVNGCVTGHFTSAEDLNLLIAKNTRLEIYVVTA...   
1   sp|Q92466|DDB2_HUMAN  MAPKKRPETQKTSEIVLRPRNKRSRSPLELEPEAKKLCAKGSGPSR...   
2   sp|P27694|RFA1_HUMAN  MVGQLSEGAIAAIMQKGDTNIKPILQVINIRPITTGNSPPRYRLLM...   
3  sp|Q92547|TOPB1_HUMAN  MSRNDKEPFFVKFLKSSDNSKCFFKALESIKEFQSEEYLQIITEEE...   
4   sp|Q15233|NONO_HUMAN  MQSNKTFNLEKQNHTPRKHHQHHHQQQHHQQQQQQPPPPPIPANGQ...   
5  sp|P16989|YBOX3_HUMAN  MSEAGEATTTTTTTLPQAPTEAAAAAPQDPAPKSPVGSGAPQAAAP...   
6  sp|Q9BQ15|SOSB1_HUMAN  MTTETFVKDIKPGLKNLNLIFIVLETGRVTKTKDGHEVRTCKVADK...   
7  sp|Q96AH0|SOSB2_HUMAN  MNRVNDPLIFIRDIKPGLKNLNVVFIVLEIGRVTKTKDGHEVRSCK...   
8   sp|P23246|SFPQ_HUMAN  MSRDRFRSRGGGGGGFHRRGGGGGRGGLHDFRSPPPGMGLNQNRGP...   
9    sp|P41134|ID1_HUMAN  MKVASGSTATAAAGPSCALKAGKTASGAGEVVRCLSEQSVAISRCA...   

  classification  type  
0    DNA BINDING    12  
1    DNA BINDING    12  
2    DNA BINDING    12  
3    DNA BINDING    12  
4    DNA BINDING    12  
5    DNA BINDING    12  
6    DNA BINDING    12  
7    DNA BINDING    12  
8    DNA BINDING    12  
9    DNA BINDING    12

In [26]:
df.shape

(63016, 4)

In [27]:
# remove the duplicate protein sequences
df = df.drop_duplicates(subset='sequence', keep="first")
df.shape

(60440, 4)

In [28]:
# scramble mouse & human protein sequences
df = df.sample(frac =1.0)

In [29]:
df.head(10)

name  \
21439          tr|D6R9Z2|D6R9Z2_HUMAN   
32824            sp|Q9UBD3|XCL2_HUMAN   
17773           sp|P70399|TP53B_MOUSE   
27872           sp|P26599|PTBP1_HUMAN   
14581          tr|Q9UBR6|Q9UBR6_HUMAN   
31879            sp|P06870|KLK1_HUMAN   
670    tr|A0A1B0GX15|A0A1B0GX15_MOUSE   
28502           sp|Q52M93|Z585B_HUMAN   
35141             sp|P30203|CD6_HUMAN   
11109          tr|M0QXU2|M0QXU2_HUMAN   

                                                sequence classification  type  
21439  MALDVKSRAKRYEKLDFLGEGQFATVYKARDKNTNQIVAIKKESLL...    DNA BINDING    12  
32824  MRLLILALLGICSLTAYIVEGVGSEVSHRRTCVSLTTQRLPVSRIK...    DNA BINDING    12  
17773  MPGEQMDPTGSQLDSDFSQQDTPCLIIEDSQPESQVLEEDAGSHFS...    DNA BINDING    12  
27872  MDGIVPDIAVGTKRGSDELFSTCVTNGPFIMSSNSASAANGNDSKK...    DNA BINDING    12  
14581  MPRAPRCRAVRSLLRSHYREVLPLATFVRRLGPQGWRLVQRGDPAA...    DNA BINDING    12  
31879  MWFLVLCLALSLGGTGAAPPIQSRIVGGWECEQHSQPWQAALYHFS...    DNA BINDING    12  
670    MKALWAVLLVTLLTGCLAEGEPEVTDQLEWQSNQPWEQALNRFWDY...    DNA BINDING    12  
28502  MPASWTSPQKSSALAPEDHGSSYEGSVSFRDVAIDFSREEWRHLDL...    DNA BINDING    12  
35141  MWLFFGITGLLTAALSGHPSPAPPDQLNTSSAESELWEPGERLPVR...    DNA BINDING    12  
11109  GEQEEYVQEGIRWTPIQYFNNKVVCDLIENKLSPPGIMSVLDDVCA...    DNA BINDING    12

## Save dataframe of sequences as a csv file

In [30]:
df.to_csv('uniprot-DNA-Binding-Feb8.csv',index = None)

proteins = pd.read_csv('uniprot-DNA-Binding-Feb8.csv')

proteins.head()

name                                           sequence  \
0  tr|D6R9Z2|D6R9Z2_HUMAN  MALDVKSRAKRYEKLDFLGEGQFATVYKARDKNTNQIVAIKKESLL...   
1    sp|Q9UBD3|XCL2_HUMAN  MRLLILALLGICSLTAYIVEGVGSEVSHRRTCVSLTTQRLPVSRIK...   
2   sp|P70399|TP53B_MOUSE  MPGEQMDPTGSQLDSDFSQQDTPCLIIEDSQPESQVLEEDAGSHFS...   
3   sp|P26599|PTBP1_HUMAN  MDGIVPDIAVGTKRGSDELFSTCVTNGPFIMSSNSASAANGNDSKK...   
4  tr|Q9UBR6|Q9UBR6_HUMAN  MPRAPRCRAVRSLLRSHYREVLPLATFVRRLGPQGWRLVQRGDPAA...   

  classification  type  
0    DNA BINDING    12  
1    DNA BINDING    12  
2    DNA BINDING    12  
3    DNA BINDING    12  
4    DNA BINDING    12

In [31]:
proteins.shape

(60440, 4)

In [33]:
proteins.type.value_counts()

12    60440
Name: type, dtype: int64